In [1]:
import numpy as np
import pandas as pd

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.models import CoherenceModel, Phrases
from gensim.models.phrases import Phraser
from gensim.models import LdaModel



# Plotting tools
import pyLDAvis.gensim_models as gensimvis
import pyLDAvis
import matplotlib.pyplot as plt
%matplotlib inline


In [2]:
from steam_reviews import ReviewLoader

appid_list = [
211420,
570940,
236430,
335300,
374320,
814380,
1245620,
485510,
1325200,
1448440,
1172380,
1774580,
265300,
678960,
606280,
378540,
644830
]

# language_list = ['english', 'schinese', 'russian']
language_list = ['russian']
text_data = []

for appid in appid_list:
    for language in language_list:
        file_path_n = 'reviews_' + str(appid) + '_' + language + '_n.json'
        reviews_n = ReviewLoader().load_from_local(file_path_n)
        review_list_n = reviews_n.review_list()
        text_data += review_list_n

len(text_data)

14362

In [3]:
text_data

['[h1]SCAM, ТЫ ЗНАЕШЬ ЭТИ ЧЕТЫРЕ БУКВЫ[/h1]\n\nКогда-то я бросил сам себе вызов пройти первую часть Dark Souls на PS3. Проблема была не в сложности игры, а в 15-20 фпс, в "Чумном городе" вовсе падало до 10 местами, еще прибавим к этому, что чумной город одна из конченых локаций в серии темных душ (салам "Помойка"). В общем-то спустя 30 часов я полностью прошел убив всех боссов без учета DLC. И вот я решил очередной раз пройти эту игру, только уже с DLC. При запуске меня ждал лок в 30 фпс, кривое управление, где вместо клавиш геймпада показаны клавиши клавиатуры, и хрен ты как это фиксанешь. При включенном геймпаде камера крутится без остановки, надо устанавливать фиксы и прочую х.у.е.т.е.н.ь чтобы фиксануть ошибки разрабов и то абсолютно все вылечить не получится. А после такого порта у них хватило совести выпустить ремастеред, в котором просто это все пофиксили, поменяли текстурку выпавших предметов и подтянули разрешение. Браво! В общем-то для меня все еще загадка каким образом из эт

In [4]:
import re

# 去除特殊字符和数字
cleaned_text = [re.sub(r'[^А-Яа-яё\s]', '', sentence) for sentence in text_data]
# 转化为小写
lowercase_text = [sentence.lower() for sentence in cleaned_text]

In [5]:
cleaned_text

[' ТЫ ЗНАЕШЬ ЭТИ ЧЕТЫРЕ БУКВЫ\n\nКогдато я бросил сам себе вызов пройти первую часть   на  Проблема была не в сложности игры а в  фпс в Чумном городе вовсе падало до  местами еще прибавим к этому что чумной город одна из конченых локаций в серии темных душ салам Помойка В общемто спустя  часов я полностью прошел убив всех боссов без учета  И вот я решил очередной раз пройти эту игру только уже с  При запуске меня ждал лок в  фпс кривое управление где вместо клавиш геймпада показаны клавиши клавиатуры и хрен ты как это фиксанешь При включенном геймпаде камера крутится без остановки надо устанавливать фиксы и прочую хуетень чтобы фиксануть ошибки разрабов и то абсолютно все вылечить не получится А после такого порта у них хватило совести выпустить ремастеред в котором просто это все пофиксили поменяли текстурку выпавших предметов и подтянули разрешение Браво В общемто для меня все еще загадка каким образом из этой параши появилась великая вселенная с учетом того что  часть в принципе выг

In [6]:
lowercase_text

[' ты знаешь эти четыре буквы\n\nкогдато я бросил сам себе вызов пройти первую часть   на  проблема была не в сложности игры а в  фпс в чумном городе вовсе падало до  местами еще прибавим к этому что чумной город одна из конченых локаций в серии темных душ салам помойка в общемто спустя  часов я полностью прошел убив всех боссов без учета  и вот я решил очередной раз пройти эту игру только уже с  при запуске меня ждал лок в  фпс кривое управление где вместо клавиш геймпада показаны клавиши клавиатуры и хрен ты как это фиксанешь при включенном геймпаде камера крутится без остановки надо устанавливать фиксы и прочую хуетень чтобы фиксануть ошибки разрабов и то абсолютно все вылечить не получится а после такого порта у них хватило совести выпустить ремастеред в котором просто это все пофиксили поменяли текстурку выпавших предметов и подтянули разрешение браво в общемто для меня все еще загадка каким образом из этой параши появилась великая вселенная с учетом того что  часть в принципе выг

In [7]:
from nltk.tokenize import word_tokenize

# 分词
tokenized_text = [word_tokenize(sentence, language="russian") for sentence in lowercase_text]

In [8]:
tokenized_text

[['ты',
  'знаешь',
  'эти',
  'четыре',
  'буквы',
  'когдато',
  'я',
  'бросил',
  'сам',
  'себе',
  'вызов',
  'пройти',
  'первую',
  'часть',
  'на',
  'проблема',
  'была',
  'не',
  'в',
  'сложности',
  'игры',
  'а',
  'в',
  'фпс',
  'в',
  'чумном',
  'городе',
  'вовсе',
  'падало',
  'до',
  'местами',
  'еще',
  'прибавим',
  'к',
  'этому',
  'что',
  'чумной',
  'город',
  'одна',
  'из',
  'конченых',
  'локаций',
  'в',
  'серии',
  'темных',
  'душ',
  'салам',
  'помойка',
  'в',
  'общемто',
  'спустя',
  'часов',
  'я',
  'полностью',
  'прошел',
  'убив',
  'всех',
  'боссов',
  'без',
  'учета',
  'и',
  'вот',
  'я',
  'решил',
  'очередной',
  'раз',
  'пройти',
  'эту',
  'игру',
  'только',
  'уже',
  'с',
  'при',
  'запуске',
  'меня',
  'ждал',
  'лок',
  'в',
  'фпс',
  'кривое',
  'управление',
  'где',
  'вместо',
  'клавиш',
  'геймпада',
  'показаны',
  'клавиши',
  'клавиатуры',
  'и',
  'хрен',
  'ты',
  'как',
  'это',
  'фиксанешь',
  'при',
  

In [9]:
from nltk.corpus import stopwords
import nltk

# 去除停用词
custom_stopwords = ['Тёмные', 'души', 'игра', 'Однорукий', 'волк', 
                    'Тени', 'умирают', 'дважды', 'elden', 'ring', 'nioh', 'wo', 'long', 'Fallen', 'Dynasty',
                   'Звёздные', 'войны', 'Lords', 'fallen', 'code', 'vein', 'Поборники', 'тьмы',
                    'Всплеск', '\n', ' ']
stop_words = set(stopwords.words('russian'))
all_stopwords = stop_words.union(custom_stopwords)
filtered_text = [[word for word in sentence if word.lower() not in all_stopwords] for sentence in tokenized_text]
filtered_text

[['знаешь',
  'четыре',
  'буквы',
  'когдато',
  'бросил',
  'вызов',
  'пройти',
  'первую',
  'часть',
  'проблема',
  'сложности',
  'игры',
  'фпс',
  'чумном',
  'городе',
  'вовсе',
  'падало',
  'местами',
  'прибавим',
  'этому',
  'чумной',
  'город',
  'одна',
  'конченых',
  'локаций',
  'серии',
  'темных',
  'душ',
  'салам',
  'помойка',
  'общемто',
  'спустя',
  'часов',
  'полностью',
  'прошел',
  'убив',
  'боссов',
  'учета',
  'решил',
  'очередной',
  'пройти',
  'игру',
  'запуске',
  'ждал',
  'лок',
  'фпс',
  'кривое',
  'управление',
  'вместо',
  'клавиш',
  'геймпада',
  'показаны',
  'клавиши',
  'клавиатуры',
  'хрен',
  'это',
  'фиксанешь',
  'включенном',
  'геймпаде',
  'камера',
  'крутится',
  'остановки',
  'устанавливать',
  'фиксы',
  'прочую',
  'хуетень',
  'фиксануть',
  'ошибки',
  'разрабов',
  'абсолютно',
  'вылечить',
  'получится',
  'такого',
  'порта',
  'хватило',
  'совести',
  'выпустить',
  'ремастеред',
  'котором',
  'просто',
 

In [10]:
# import nltk
# from nltk.stem import SnowballStemmer

# stemmer = SnowballStemmer("english")

# stemmed_text = [[stemmer.stem(word) for word in sentence] for sentence in filtered_text]

In [11]:
# 准备文本数据和分词
# 这里假设你已经有了一个文本数据集并进行了分词处理

# 创建词典和文档-词频矩阵
dictionary = corpora.Dictionary(filtered_text)  # your_corpus是已分词的文本数据
corpus = [dictionary.doc2bow(text) for text in filtered_text]

# 选择不同主题数进行训练和评估
start = 3  # 主题数的起始值
limit = 10  # 主题数的结束值
step = 1  # 主题数的步长

coherence_scores = []  # 用于存储主题一致性分数
perplexity_scores = []  # 用于存储困惑度分数

for num_topics in range(start, limit, step):
    lda_model = LdaModel(corpus, num_topics=num_topics, id2word=dictionary, passes=15)
    
    # 计算主题一致性分数
    coherence_model = CoherenceModel(model=lda_model, texts=filtered_text, dictionary=dictionary, coherence='c_v')
    coherence_score = coherence_model.get_coherence()
    coherence_scores.append(coherence_score)
    
    # 计算困惑度分数
    perplexity_score = lda_model.log_perplexity(corpus)
    perplexity_scores.append(perplexity_score)

# 打印结果
print("主题数 vs. 主题一致性分数:")
for num_topics, coherence_score in zip(range(start, limit, step), coherence_scores):
    print(f"{num_topics} 主题: {coherence_score}")

print("\n主题数 vs. 困惑度分数:")
for num_topics, perplexity_score in zip(range(start, limit, step), perplexity_scores):
    print(f"{num_topics} 主题: {perplexity_score}")

主题数 vs. 主题一致性分数:
3 主题: 0.3544384558158195
4 主题: 0.39060496971817593
5 主题: 0.4653031357280416
6 主题: 0.4168117493605356
7 主题: 0.5163821395350274
8 主题: 0.4763774648542436
9 主题: 0.5828712493286705

主题数 vs. 困惑度分数:
3 主题: -9.582990781621646
4 主题: -9.582988681027548
5 主题: -9.676469458398277
6 主题: -9.836295658175592
7 主题: -10.019408847218756
8 主题: -10.27250098296485
9 主题: -10.631648978086007


In [10]:
# 创建词袋模型
dictionary = corpora.Dictionary(filtered_text)
# 将文本数据转化为文档-词频矩阵
corpus = [dictionary.doc2bow(text) for text in filtered_text]

In [ ]:
# 训练LDA模型
num_topics = 10
lda_model = LdaModel(corpus, num_topics=num_topics, id2word=dictionary, passes=15, random_state=42)

In [12]:
# 查看主题
topics = lda_model.print_topics(num_words=10)
for topic in topics:
    print(topic)

(0, '0.010*"сервера" + 0.007*"серверверните" + 0.005*"классов" + 0.004*"нравятся" + 0.004*"верните" + 0.004*"суки" + 0.003*"инди" + 0.003*"бабадзаки" + 0.003*"включите" + 0.002*"уважаемые"')
(1, '0.005*"ебал" + 0.004*"танцы" + 0.003*"базе" + 0.003*"зашло" + 0.003*"сосал" + 0.003*"тысяч" + 0.003*"топографический" + 0.003*"начинаются" + 0.003*"хм" + 0.003*"духи"')
(2, '0.019*"персонаж" + 0.015*"моргает" + 0.006*"предзаказ" + 0.006*"черта" + 0.005*"стартовой" + 0.005*"кал" + 0.003*"зацепила" + 0.002*"сломанная" + 0.002*"усилить" + 0.002*"геймплейные"')
(3, '0.007*"повторяются" + 0.005*"озвучка" + 0.004*"надоело" + 0.004*"сырая" + 0.003*"почтение" + 0.003*"отсюда" + 0.003*"бла" + 0.003*"постараться" + 0.003*"стар" + 0.003*"замки"')
(4, '0.007*"игры" + 0.006*"фпс" + 0.005*"стоит" + 0.005*"денег" + 0.005*"части" + 0.005*"хуже" + 0.005*"рублей" + 0.004*"игру" + 0.004*"пвп" + 0.004*"оптимизация"')
(5, '0.010*"н" + 0.008*"создать" + 0.006*"е" + 0.005*"б" + 0.005*"л" + 0.004*"стан" + 0.004*"чё" 

In [13]:
pyLDAvis.enable_notebook()
lda_display = gensimvis.prepare(lda_model, corpus, dictionary)
pyLDAvis.display(lda_display)

In [30]:
pyLDAvis.save_html(lda_display, 'output_ru_n.html')

#### 

In [31]:
import pickle

# 假设你的LDA模型命名为lda_model
with open('lda_model_ru_t10.pkl', 'wb') as f:
    pickle.dump(lda_model, f)

In [11]:
import pickle

# 加载LDA模型
with open('lda_model_ru_t10.pkl', 'rb') as f:
    lda_model = pickle.load(f)

In [15]:
from steam_reviews import ReviewLoader

appid_list = [
211420,
570940,
236430,
335300,
374320,
814380,
1245620,
485510,
1325200,
1448440,
1172380,
1774580,
265300,
678960,
606280,
378540,
644830
]

# language_list = ['english', 'schinese', 'russian']
language_list = ['russian']

topic_mapping = {0: 9, 1: 7, 2: 10, 3: 4, 4: 3, 5: 5, 6: 6, 7: 2, 8: 1, 9: 8}
group_mapping = {3: 0, 4: 0, 5: 0, 10: 0, 2: 1, 9: 2, 1: 3, 6: 4, 7: 5, 8: 5}
index = 0
results = []

for appid in appid_list:
    for language in language_list:
        result_list = [0] * 6
        file_path_n = 'reviews_' + str(appid) + '_' + language + '_n.json'
        reviews_n = ReviewLoader().load_from_local(file_path_n)
        review_list_n = reviews_n.review_list()
        for review in review_list_n:
            topics = lda_model[corpus[index]]
            top_topic = max(topics, key=lambda x: x[1])  # 找到概率最高的主题
            topic_index = topic_mapping[top_topic[0]]
            result_list[group_mapping[topic_index]] += 1
            index += 1
            
        print(result_list)    
        results.append(result_list)

[51, 210, 38, 280, 8, 20]
[187, 149, 74, 563, 13, 18]
[55, 121, 35, 335, 7, 11]
[195, 260, 123, 1126, 36, 33]
[274, 455, 233, 1386, 36, 59]
[29, 99, 41, 492, 6, 16]
[282, 763, 263, 1979, 53, 66]
[16, 91, 20, 259, 2, 9]
[6, 35, 10, 81, 0, 1]
[5, 10, 5, 35, 2, 0]
[59, 79, 40, 668, 15, 17]
[33, 33, 28, 99, 0, 1]
[54, 152, 41, 668, 9, 19]
[29, 52, 30, 420, 5, 13]
[29, 34, 6, 335, 5, 5]
[25, 17, 9, 136, 3, 3]
[25, 26, 2, 69, 1, 1]


In [16]:
import csv

# 指定要保存的文件名
filename = "output.csv"

# 使用 csv 模块创建 CSV 文件并写入数据
with open(filename, mode="w", newline="") as file:
    writer = csv.writer(file, delimiter=",", quotechar='"', quoting=csv.QUOTE_MINIMAL)

    # 遍历二维列表并写入 CSV 文件
    for row in results:
        writer.writerow(row)